# Web Scraping Job Boards: Indeed
This tool has evolved from Jean-Nicholas Hould's Web Scraping for Beers web page.  This example programme uses the Indeed Job Board to search for advertised roles.  The code constructs a text string URL comprising the search term, posting age and page number.  It cycles through each page locating the HTML tags which define distinct jobs and stores the relevant job details.

In [1]:
# Import relevant Python packages
# Python 3.6 :: Anaconda 4.3.1 (x86_64)
# pandas==0.19.2
# beautifulsoup4==4.5.3
from urllib.request import urlopen
from bs4 import BeautifulSoup
import pandas as pd
import re
import time

In [2]:
# Determines if URL (httpstring) is a valid web page link.
# Module attempts to open URL and returns True if successful or False if unsucessful
def is_link(httpstring):
    try:
        html = urlopen(httpstring)
    except IOError:
        weblink= False
    else:
        weblink = True
        html.close
    return ( weblink)

In [4]:
def get_all_jobs():
    # List of job search terms
    entertopic = ["Data+Scientist","Machine+Learning","Artificial+Intelligence","Data+Science"]
    # Number of search pages to cycle through for each search term
    # It is advisable to try each search term on the website and confirm the relevant number of pages to use 
    numpages = [8,25,9,17]

    # Initialise the Panda frame 'jobs'
    jobs = []
    # Loop through each search term (j represents the search term index in array 'entertopic')
    for j in range(0,4):
        # Loop through each URL page (i represents the page index in array 'numpages')
        for i in range(0, numpages[j]):
            # Examine the website URL to understand its structure and the parameters
            # Create the URL using the Indeed stem, search term, job age, number of jobs per webpage and page number
            httpstring = "https://www.indeed.co.uk/jobs?&as_phr=" + entertopic[j] + "&fromage=15&limit=50&sort=date&start=" + str(i*50)
            print(i,httpstring)

            # Include a delay between loading webpages.  This is good etiquette to avoid impacting website performance 
            time.sleep(4)
            # Check whether the URL created is a valid webpage
            if is_link(httpstring):
                html = urlopen(httpstring)
                html_soup = BeautifulSoup(html, 'html.parser')

                # Using Beautiful Soup select all HTML 'div' tags on the webpage
                all_div_tags = html_soup.find_all("div")
                # Step through each HTML 'div' tag 
                for h2_tags in all_div_tags:
                    # Initialise variables which will hold the job information
                    websource = "Indeed"
                    job_title = ""
                    joblocation = ""
                    jobsalary = ""
                    employer = ""
                    weblink = ""
                    jobtype = ""
                    jobdetail = ""
                    posteddate = ""
                    # Find HTML 'h2' tag. Check one exists
                    if h2_tags.h2 != None:
                        # Job title is text in <h2> <a> tag
                        job_title = h2_tags.h2.a.text
                        # Web link is href in <h2> <a> tag
                        weblink='https://www.indeed.co.uk' + h2_tags.h2.a['href']

                        # Find HTML 'span' tag which has 'class'='location'. Check one exists
                        if h2_tags.find("span",{'class': 'location'}) != None:
                            # Job location is text in 'span' tag which has 'class' = 'location'
                            joblocation = h2_tags.find("span",{'class': 'location'}).text

                        # Find HTML 'span' tag which has 'class'='company'. Check one exists
                        employer_tag = h2_tags.find("span",{'class':'company'})
                        if employer_tag != None:
                            employer_tag_a = employer_tag.a
                            # Employer is text in <a> tag of 'span' tag which has 'class'='company' if it exists
                            if employer_tag_a != None:
                                employer = employer_tag_a.get_text().replace('\n','')

                            elif employer_tag != None:
                                employer = employer_tag.get_text().replace('\n','')

                        # Find HTML 'span' tag which has 'class'='no-wrap'. Check one exists
                        salary_tag = h2_tags.find("span",{'class':'no-wrap'})
                        if salary_tag != None:
                            # Salary is text in 'span' tag which has 'class'='no-wrap'
                            jobsalary = salary_tag.text.replace('\n','')
                        # Assign job details to 'job_list' dataframe 
                        job_list = {
                            "websource" : websource,
                            "jobtitle" : job_title,
                            "Joblocation" : joblocation,
                            "jobsalary" : jobsalary,
                            "employer" : employer,
                            "weblink" : weblink,
                            "jobtype" : jobtype,
                            "posteddate" : posteddate,
                            "jobdetail" : jobdetail,
                        }        
                        jobs.append(job_list)
     
    return jobs

In [5]:
job_list = get_all_jobs()    
# Add job_list to Panda dataframe 'jl'
jl = pd.DataFrame(job_list)
# Display the contents of the dataframe 'jl'
jl

0 https://www.indeed.co.uk/jobs?&as_phr=Data+Science&fromage=15&limit=50&sort=date&start=0
1 https://www.indeed.co.uk/jobs?&as_phr=Data+Science&fromage=15&limit=50&sort=date&start=50
2 https://www.indeed.co.uk/jobs?&as_phr=Data+Science&fromage=15&limit=50&sort=date&start=100
3 https://www.indeed.co.uk/jobs?&as_phr=Data+Science&fromage=15&limit=50&sort=date&start=150
4 https://www.indeed.co.uk/jobs?&as_phr=Data+Science&fromage=15&limit=50&sort=date&start=200
5 https://www.indeed.co.uk/jobs?&as_phr=Data+Science&fromage=15&limit=50&sort=date&start=250
6 https://www.indeed.co.uk/jobs?&as_phr=Data+Science&fromage=15&limit=50&sort=date&start=300
7 https://www.indeed.co.uk/jobs?&as_phr=Data+Science&fromage=15&limit=50&sort=date&start=350
8 https://www.indeed.co.uk/jobs?&as_phr=Data+Science&fromage=15&limit=50&sort=date&start=400
9 https://www.indeed.co.uk/jobs?&as_phr=Data+Science&fromage=15&limit=50&sort=date&start=450
10 https://www.indeed.co.uk/jobs?&as_phr=Data+Science&fromage=15&limit=50

Joblocation  \
0                    London   
1                    London   
2                   Reading   
3                    London   
4                   Belfast   
5                   England   
6                    London   
7                    London   
8                    London   
9                    London   
10                   London   
11                   London   
12                   London   
13                   London   
14             Newport NP10   
15                   London   
16                   London   
17                   London   
18                   London   
19                   London   
20          North Yorkshire   
21                   London   
22                   Marlow   
23                   London   
24                   London   
25               Sellafield   
26                   London   
27                   London   
28                   Romsey   
29                   London   
..                      ...   
812           Brentford TW8   
813               Cambridge   
814                York YO1   
815                  London   
816             London WC2A   
817          United Kingdom   
818          United Kingdom   
819          United Kingdom   
820              London SE1   
821                  London   
822                  London   
823  Hammersmith and Fulham   
824              Home Based   
825             London WC2A   
826          United Kingdom   
827                  London   
828                  London   
829               Edinburgh   
830             London EC1V   
831                  London   
832                  London   
833                  London   
834                  London   
835                  London   
836                  London   
837                  London   
838                Brighton   
839                  Surrey   
840          West Yorkshire   
841          United Kingdom   

                                              employer jobdetail  \
0                                      GreenTomatoCars             
1                                             Adhunter             
2                                                IQVIA             
3                        Hitachi Consulting UK Limited             
4                                             ShopKeep             
5                                 University of London             
6                        Hitachi Consulting UK Limited             
7                                  The Economist Group             
8                                    PeoplePerHour.com             
9                        Hitachi Consulting UK Limited             
10                                             Harnham             
11                                       Deutsche Bank             
12                                        Mapmechanics             
13                            Birch & James Associates             
14                      Office for National Statistics             
15                                       Xcede Digital             
16                                     Vertus Partners             
17                                             Harnham             
18                                       Xcede Digital             
19                                       Xcede Digital             
20                             Aspire Data Recruitment             
21                                              Signal             
22                                       SAS Institute             
23                             Digitech Resourcing Ltd             
24                                Lloyds Banking Group             
25                                                Arup             
26                                       Xcede Digital             
27                      Networking People (UK) Limited             
28                                         Spectrum IT             
29                                     kdr Recruitmen

In [6]:
# Create a new dataframe with reordered fields
jlnew = jl[['websource','employer','jobtitle','Joblocation','jobsalary','jobtype','posteddate','jobdetail','weblink']]
# Export the fields of the 'jlnew' dataframe to a new CSV file
jlnew.to_csv('Jobs_Indeed_20180421.csv')
jlnew.iloc[0,0]

'Indeed'